In [ ]:
import pandas as pd
import numpy as np
import psycopg2 as pg
import geopandas as gpd
from tqdm.auto import tqdm
tqdm.pandas()

: 

In [2]:
# Тут нужно включить впн
engine = pg.connect("dbname='city_db_final' user='postgres' host='10.32.1.107' port='5432' password='postgres'")

In [18]:
GROUPS = ('Детский сад','Бассейн','Библиотека',  'Детская поликлиника', 'Поликлиника', 'Школа', 
          'Спортивная площадка', 'Зоопарк', 'Кинотеатр', 'Музей', 'Театр/Концертный зал', 'Больница', 'Детская больница',
          'Учреждение высшего профессионального образования', 'Учреждение среднего профессионального образования')

In [19]:
matrix = pd.read_csv('/home/gk/Documents/matrix_mmg.csv').set_index('id')
blocks_geom = gpd.read_file('/home/gk/Downloads/Telegram Desktop/blocks_with_living_buildings.geojson')


for SUB_GROUP in tqdm(GROUPS):
    df = pd.read_sql(f"select DISTINCT(block_id) as service_blocks_id from all_services where city_service_type in ('{SUB_GROUP}') "\
                      "and city_id=1 ORDER BY block_id asc", con=engine)

    living_blocks = blocks_geom.loc[blocks_geom.is_living==True, ['id', 'geometry']].sort_values(by='id').reset_index(drop=True)

    display(matrix.loc[matrix.index.isin(df.service_blocks_id.astype('Int64')), matrix.columns.isin(living_blocks['id'].astype(str))])
    blocks_list = matrix.loc[matrix.index.isin(df.service_blocks_id.astype('Int64')), matrix.columns.isin(living_blocks['id'].astype(str))].min(axis=0)
    display(blocks_list)

    blocks_list = blocks_list.to_frame(name='time_min').reset_index()
    blocks_list['index'] = blocks_list['index'].astype(int)

    living_blocks = living_blocks.merge(blocks_list, left_on='id', right_on='index').drop(columns='index')

    display(living_blocks)
    # 1/0

    if SUB_GROUP == 'Детский сад':
        conditions = [
        (living_blocks['time_min'] < 4),
        (living_blocks['time_min'] >= 4) & (living_blocks['time_min'] < 7),
        (living_blocks['time_min'] >= 7) & (living_blocks['time_min'] < 10),
        (living_blocks['time_min'] >= 10) & (living_blocks['time_min'] < 14),
        (living_blocks['time_min'] >= 14)
        ]
    
    elif SUB_GROUP in('Детская поликлиника', 'Поликлиника'):
        conditions = [
        (living_blocks['time_min'] < 5),
        (living_blocks['time_min'] >= 5) & (living_blocks['time_min'] < 10),
        (living_blocks['time_min'] >= 10) & (living_blocks['time_min'] < 15),
        (living_blocks['time_min'] >= 15) & (living_blocks['time_min'] < 20),
        (living_blocks['time_min'] >= 20)
        ]

    elif SUB_GROUP in ('Школа', 'Библиотека', 'Бассейн', 'Спортивная площадка'):
        conditions = [
        (living_blocks['time_min'] < 10),
        (living_blocks['time_min'] >= 10) & (living_blocks['time_min'] < 20),
        (living_blocks['time_min'] >= 20) & (living_blocks['time_min'] < 30),
        (living_blocks['time_min'] >= 30) & (living_blocks['time_min'] < 40),
        (living_blocks['time_min'] >= 40)
        ]

    elif SUB_GROUP in ('Зоопарк', 'Кинотеатр', 'Музей', 'Театр/Концертный зал', 'Больница', 'Детская больница',
          'Учреждение высшего профессионального образования', 'Учреждение среднего профессионального образования'):
        conditions = [
        (living_blocks['time_min'] < 20),
        (living_blocks['time_min'] >= 20) & (living_blocks['time_min'] < 40),
        (living_blocks['time_min'] >= 40) & (living_blocks['time_min'] < 60),
        (living_blocks['time_min'] >= 60) & (living_blocks['time_min'] < 70),
        (living_blocks['time_min'] >= 70)
        ]

    values = [5,4,3,2,1]
    living_blocks['mark'] = np.select(conditions, values)
    SUB_GROUP = SUB_GROUP.replace('/', '_')
    living_blocks.sort_values(by='mark').to_file(f'sasha_morozov15_serv/sasha_morozov_{SUB_GROUP}.geojson')
                 

  0%|          | 0/15 [00:00<?, ?it/s]

2      3      4      5      6      7      8     10     11     12  \
id                                                                           
2       0.0   84.8   83.1   42.4   73.9   55.7  292.4   69.3   80.1  108.8   
11     85.9   37.6   52.9   56.4   33.8   92.4  318.5   78.1    0.0   85.0   
13    151.2   82.2   79.4  119.2   86.6  165.7  399.5  117.8  108.5   88.8   
15     46.7   88.3   89.5   56.8   73.1   31.9  270.6   88.6   73.3  120.2   
16     86.4   66.3   64.8   51.8   70.9  110.9  303.5   20.0   84.1   77.9   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
6242  130.7  173.8  171.8  137.6  169.1  137.7  171.8  134.8  175.6  188.4   
6264  121.6  164.7  162.7  128.5  160.0  150.5  184.6  125.7  166.5  179.3   
6306   79.8   35.0   31.1   39.4   39.6  100.5  316.8   33.8   61.3   49.7   
6307   78.6   19.1   29.9   45.9    4.1   84.9  329.9   55.1   35.1   62.0   
6308   89.7   43.0   24.4   49.3   44.2  110.4  326.7   43.7   69.2   33.2   

      ...   6288   6290   6291   6292   6295   6306   6307   6308   6309  \
id    ...                                                                  
2     ...  249.6  253.7  238.6  238.4  244.8   78.0   74.0   87.5   32.1   
11    ...  232.8  234.9  239.7  236.4  236.2   57.7   31.6   65.9   70.0   
13    ...  180.1  182.2  187.0  183.7  183.5  100.8   82.6   85.1  143.2   
15    ...  266.4  268.5  265.6  265.4  269.8   91.4   73.6  100.9   19.4   
16    ...  221.0  223.1  227.9  224.6  224.4   45.8   66.9   55.3   85.1   
...   ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
6242  ...  193.6  197.7  182.6  182.4  188.8  156.3  169.2  165.8  143.5   
6264  ...  184.5  188.6  173.5  173.3  179.7  147.2  160.1  156.7  134.4   
6306  ...  192.8  194.9  199.7  196.4  196.2    0.0   35.6   27.1   74.7   
6307  ...  209.4  211.5  216.3  213.0  212.8   34.7    0.0   42.9   62.5   
6308  ...  184.4  186.5  191.3  188.0  187.8   25.8   40.7    0.0   84.6   

       6310  
id           
2      47.4  
11     56.8  
13    114.2  
15     60.8  
16     48.7  
...     ...  
6242  142.6  
6264  133.5  
6306   38.3  
6307   43.7  
6308   48.2  

[693 rows x 4023 columns]

2        0.0
3       12.5
4        8.4
5        5.5
6        4.1
        ... 
6306     0.0
6307     0.0
6308     0.0
6309     7.2
6310     7.2
Length: 4023, dtype: float64

id                                           geometry  time_min
0        2  MULTIPOLYGON (((30.27569 60.01187, 30.27273 60...       0.0
1        3  MULTIPOLYGON (((30.37142 59.92849, 30.37013 59...      12.5
2        4  MULTIPOLYGON (((30.33351 59.91790, 30.33186 59...       8.4
3        5  MULTIPOLYGON (((30.30415 59.96934, 30.30406 59...       5.5
4        6  MULTIPOLYGON (((30.36352 59.94154, 30.36056 59...       4.1
...    ...                                                ...       ...
4018  6306  MULTIPOLYGON (((30.29618 59.93163, 30.30080 59...       0.0
4019  6307  MULTIPOLYGON (((30.36050 59.94085, 30.36048 59...       0.0
4020  6308  MULTIPOLYGON (((30.29744 59.91355, 30.30548 59...       0.0
4021  6309  MULTIPOLYGON (((30.31711 60.01711, 30.31678 60...       7.2
4022  6310  MULTIPOLYGON (((30.30157 59.96321, 30.30233 59...       7.2

[4023 rows x 3 columns]

  0%|          | 0/15 [00:00<?, ?it/s]


ZeroDivisionError: division by zero

In [3]:
# matrix = pd.read_csv('/home/gk/Documents/matrix_mmg.csv').set_index('id')
matrix = pd.read_csv('/home/gk/Downloads/matrix_mmg_sev.csv').set_index('id')
# blocks_geom = gpd.read_file('/home/gk/Downloads/blocks_krasnodar.geojson') 
# blocks_geom = gpd.read_file('/home/gk/Downloads/Telegram Desktop/blocks_with_living_buildings.geojson') 

In [4]:
blocks_geom = gpd.read_postgis('select id, geometry as geom ' \
          'from blocks where city_id=5', con=engine)

/home/gk/vscode/metrics_accs/CityGeoTools/venv/lib/python3.9/site-packages/geopandas/io/sql.py:158: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql(


In [5]:
m = matrix.median().to_frame(name='median').reset_index(drop=False).round(0)
m['index'] = m['index'].astype(int)
m

index  median
0    14483    79.0
1    14484    76.0
2    14485    60.0
3    14486    75.0
4    14487    75.0
..     ...     ...
804  15291    94.0
805  15292   113.0
806  15293   131.0
807  15294   128.0
808  15295   127.0

[809 rows x 2 columns]

In [6]:
blocks_geom

id                                               geom
0    14483  POLYGON ((33.54778 44.55518, 33.54785 44.55522...
1    14484  POLYGON ((33.55020 44.56768, 33.55020 44.56768...
2    14485  POLYGON ((33.52727 44.59087, 33.52747 44.59062...
3    14486  POLYGON ((33.55121 44.56685, 33.55183 44.56645...
4    14487  POLYGON ((33.55015 44.56759, 33.55056 44.56731...
..     ...                                                ...
804  15291  POLYGON ((33.41918 44.56473, 33.41918 44.56473...
805  15292  POLYGON ((33.40750 44.56203, 33.40731 44.56212...
806  15293  POLYGON ((33.40799 44.57494, 33.40829 44.57529...
807  15294  POLYGON ((33.40885 44.57383, 33.40856 44.57396...
808  15295  POLYGON ((33.40882 44.57374, 33.40867 44.57311...

[809 rows x 2 columns]

In [7]:
blocks_geom[['id', 'geom']].merge(m, left_on='id', right_on='index').drop(columns=['index']).to_file('median_accs_sev.geojson')

In [20]:
x = matrix.loc[matrix.index.isin(df.service_blocks_id.astype('Int64')), matrix.columns.isin(living_blocks['id'].astype(str))]
x

2      3      4      5      6      7      8     10     11     12  \
id                                                                           
2       0.0   84.8   83.1   42.4   73.9   55.7  292.4   69.3   80.1  108.8   
11     85.9   37.6   52.9   56.4   33.8   92.4  318.5   78.1    0.0   85.0   
13    151.2   82.2   79.4  119.2   86.6  165.7  399.5  117.8  108.5   88.8   
15     46.7   88.3   89.5   56.8   73.1   31.9  270.6   88.6   73.3  120.2   
16     86.4   66.3   64.8   51.8   70.9  110.9  303.5   20.0   84.1   77.9   
...     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
6242  130.7  173.8  171.8  137.6  169.1  137.7  171.8  134.8  175.6  188.4   
6264  121.6  164.7  162.7  128.5  160.0  150.5  184.6  125.7  166.5  179.3   
6306   79.8   35.0   31.1   39.4   39.6  100.5  316.8   33.8   61.3   49.7   
6307   78.6   19.1   29.9   45.9    4.1   84.9  329.9   55.1   35.1   62.0   
6308   89.7   43.0   24.4   49.3   44.2  110.4  326.7   43.7   69.2   33.2   

      ...   6288   6290   6291   6292   6295   6306   6307   6308   6309  \
id    ...                                                                  
2     ...  249.6  253.7  238.6  238.4  244.8   78.0   74.0   87.5   32.1   
11    ...  232.8  234.9  239.7  236.4  236.2   57.7   31.6   65.9   70.0   
13    ...  180.1  182.2  187.0  183.7  183.5  100.8   82.6   85.1  143.2   
15    ...  266.4  268.5  265.6  265.4  269.8   91.4   73.6  100.9   19.4   
16    ...  221.0  223.1  227.9  224.6  224.4   45.8   66.9   55.3   85.1   
...   ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
6242  ...  193.6  197.7  182.6  182.4  188.8  156.3  169.2  165.8  143.5   
6264  ...  184.5  188.6  173.5  173.3  179.7  147.2  160.1  156.7  134.4   
6306  ...  192.8  194.9  199.7  196.4  196.2    0.0   35.6   27.1   74.7   
6307  ...  209.4  211.5  216.3  213.0  212.8   34.7    0.0   42.9   62.5   
6308  ...  184.4  186.5  191.3  188.0  187.8   25.8   40.7    0.0   84.6   

       6310  
id           
2      47.4  
11     56.8  
13    114.2  
15     60.8  
16     48.7  
...     ...  
6242  142.6  
6264  133.5  
6306   38.3  
6307   43.7  
6308   48.2  

[693 rows x 4023 columns]

In [21]:
x.loc[:, '4926'].sort_values()

id
5068      6.8
5489      9.7
5481     10.1
5477     15.1
2573     68.9
        ...  
3544    323.4
3543    324.7
2191    325.1
3703    347.9
3721    354.4
Name: 4926, Length: 693, dtype: float64

In [20]:
# SUB_GROUP = ('Школа', 'Библиотека', 'Бассейн', 'Спортивная площадка')

In [ ]:
# df = pd.read_sql(f'select DISTINCT(block_id) as service_blocks_id from all_services where city_service_type in {SUB_GROUP} '\
#                  'and city_id=1 ORDER BY block_id asc', con=engine)
# display(df)

In [23]:
SUB_GROUP = ('Детский сад')

In [24]:
df = pd.read_sql(f"select DISTINCT(block_id) as service_blocks_id from all_services where city_service_type in ('{SUB_GROUP}') "\
                 "and city_id=1 ORDER BY block_id asc", con=engine)
display(df)

service_blocks_id
0                    2
1                   11
2                   13
3                   15
4                   16
..                 ...
688               6242
689               6264
690               6306
691               6307
692               6308

[693 rows x 1 columns]

In [27]:
matrix = pd.read_csv('/home/gk/Documents/matrix_mmg.csv').set_index('id')
# matrix = pd.read_csv('вставь сюда путь до матрицы').set_index('id')

In [28]:
matrix

2     3     4     5     6      7      8    10    11     12  ...  \
id                                                                   ...   
2      0.0  84.8  83.1  42.4  73.9   55.7  292.4  69.3  80.1  108.8  ...   
3     82.6   0.0  28.1  50.6  21.9   97.8  332.6  53.3  39.3   60.2  ...   
4     85.3  29.4   0.0  52.1  30.1  102.8  332.7  51.5  55.1   46.1  ...   
5     47.4  53.0  51.3   0.0  42.1   68.1  298.6  40.3  53.2   76.9  ...   
6     77.6  23.0  31.2  44.9   0.0   83.9  328.9  57.9  36.5   62.7  ...   
...    ...   ...   ...   ...   ...    ...    ...   ...   ...    ...  ...   
6306  79.8  35.0  31.1  39.4  39.6  100.5  316.8  33.8  61.3   49.7  ...   
6307  78.6  19.1  29.9  45.9   4.1   84.9  329.9  55.1  35.1   62.0  ...   
6308  89.7  43.0  24.4  49.3  44.2  110.4  326.7  43.7  69.2   33.2  ...   
6309  31.5  78.7  77.6  42.9  64.5   29.6  271.7  75.7  67.4  103.1  ...   
6310  51.9  51.5  48.0  15.2  43.4   72.6  303.0  33.0  55.6   67.9  ...   

       6301   6302  6303  6304   6305  6306  6307  6308  6309  6310  
id                                                                   
2     158.1   60.9  55.9  56.4   74.3  78.0  74.0  87.5  32.1  47.4  
3     109.7   94.3  98.3  68.3  107.0  32.9  17.9  41.1  75.4  45.6  
4      95.4  100.5  93.7  67.9  113.2  29.1  26.6  24.2  76.4  48.3  
5     125.4   69.0  58.8  57.3   82.4  44.8  42.2  54.3  43.2  13.9  
6     112.0   80.4  95.6  72.9   93.1  38.6   4.1  46.3  61.5  45.3  
...     ...    ...   ...   ...    ...   ...   ...   ...   ...   ...  
6306   98.2  101.4  80.1  50.2  114.8   0.0  35.6  27.1  74.7  38.3  
6307  112.5   81.4  96.6  70.1   94.1  34.7   0.0  42.9  62.5  43.7  
6308   89.8  111.3  90.0  60.1  124.7  25.8  40.7   0.0  84.6  48.2  
6309  152.4   43.4  70.7  66.3   55.1  77.9  65.0  86.8   0.0  47.9  
6310  116.4   73.5  62.4  53.4   86.9  35.8  43.5  45.3  46.7   0.0  

[5577 rows x 5577 columns]

In [29]:
blocks_geom = gpd.read_file('/home/gk/Downloads/Telegram Desktop/blocks_with_living_buildings.geojson') 
living_blocks = blocks_geom.loc[blocks_geom.is_living==True, ['id', 'geometry']].sort_values(by='id').reset_index(drop=True)
living_blocks

id                                           geometry
0        2  MULTIPOLYGON (((30.27569 60.01187, 30.27273 60...
1        3  MULTIPOLYGON (((30.37142 59.92849, 30.37013 59...
2        4  MULTIPOLYGON (((30.33351 59.91790, 30.33186 59...
3        5  MULTIPOLYGON (((30.30415 59.96934, 30.30406 59...
4        6  MULTIPOLYGON (((30.36352 59.94154, 30.36056 59...
...    ...                                                ...
4018  6306  MULTIPOLYGON (((30.29618 59.93163, 30.30080 59...
4019  6307  MULTIPOLYGON (((30.36050 59.94085, 30.36048 59...
4020  6308  MULTIPOLYGON (((30.29744 59.91355, 30.30548 59...
4021  6309  MULTIPOLYGON (((30.31711 60.01711, 30.31678 60...
4022  6310  MULTIPOLYGON (((30.30157 59.96321, 30.30233 59...

[4023 rows x 2 columns]

In [30]:
matrix

2     3     4     5     6      7      8    10    11     12  ...  \
id                                                                   ...   
2      0.0  84.8  83.1  42.4  73.9   55.7  292.4  69.3  80.1  108.8  ...   
3     82.6   0.0  28.1  50.6  21.9   97.8  332.6  53.3  39.3   60.2  ...   
4     85.3  29.4   0.0  52.1  30.1  102.8  332.7  51.5  55.1   46.1  ...   
5     47.4  53.0  51.3   0.0  42.1   68.1  298.6  40.3  53.2   76.9  ...   
6     77.6  23.0  31.2  44.9   0.0   83.9  328.9  57.9  36.5   62.7  ...   
...    ...   ...   ...   ...   ...    ...    ...   ...   ...    ...  ...   
6306  79.8  35.0  31.1  39.4  39.6  100.5  316.8  33.8  61.3   49.7  ...   
6307  78.6  19.1  29.9  45.9   4.1   84.9  329.9  55.1  35.1   62.0  ...   
6308  89.7  43.0  24.4  49.3  44.2  110.4  326.7  43.7  69.2   33.2  ...   
6309  31.5  78.7  77.6  42.9  64.5   29.6  271.7  75.7  67.4  103.1  ...   
6310  51.9  51.5  48.0  15.2  43.4   72.6  303.0  33.0  55.6   67.9  ...   

       6301   6302  6303  6304   6305  6306  6307  6308  6309  6310  
id                                                                   
2     158.1   60.9  55.9  56.4   74.3  78.0  74.0  87.5  32.1  47.4  
3     109.7   94.3  98.3  68.3  107.0  32.9  17.9  41.1  75.4  45.6  
4      95.4  100.5  93.7  67.9  113.2  29.1  26.6  24.2  76.4  48.3  
5     125.4   69.0  58.8  57.3   82.4  44.8  42.2  54.3  43.2  13.9  
6     112.0   80.4  95.6  72.9   93.1  38.6   4.1  46.3  61.5  45.3  
...     ...    ...   ...   ...    ...   ...   ...   ...   ...   ...  
6306   98.2  101.4  80.1  50.2  114.8   0.0  35.6  27.1  74.7  38.3  
6307  112.5   81.4  96.6  70.1   94.1  34.7   0.0  42.9  62.5  43.7  
6308   89.8  111.3  90.0  60.1  124.7  25.8  40.7   0.0  84.6  48.2  
6309  152.4   43.4  70.7  66.3   55.1  77.9  65.0  86.8   0.0  47.9  
6310  116.4   73.5  62.4  53.4   86.9  35.8  43.5  45.3  46.7   0.0  

[5577 rows x 5577 columns]

In [31]:
blocks_list = matrix.loc[matrix.index.isin(df.service_blocks_id.astype('Int64')), matrix.columns.isin(living_blocks['id'].astype(str))].min(axis=0)
blocks_list = blocks_list.to_frame(name='time_min').reset_index()

In [32]:
blocks_list['index'] = blocks_list['index'].astype(int)

In [33]:
living_blocks = living_blocks.merge(blocks_list, left_on='id', right_on='index').drop(columns='index')
living_blocks

id                                           geometry  time_min
0        2  MULTIPOLYGON (((30.27569 60.01187, 30.27273 60...       0.0
1        3  MULTIPOLYGON (((30.37142 59.92849, 30.37013 59...      12.5
2        4  MULTIPOLYGON (((30.33351 59.91790, 30.33186 59...       8.4
3        5  MULTIPOLYGON (((30.30415 59.96934, 30.30406 59...       5.5
4        6  MULTIPOLYGON (((30.36352 59.94154, 30.36056 59...       4.1
...    ...                                                ...       ...
4018  6306  MULTIPOLYGON (((30.29618 59.93163, 30.30080 59...       0.0
4019  6307  MULTIPOLYGON (((30.36050 59.94085, 30.36048 59...       0.0
4020  6308  MULTIPOLYGON (((30.29744 59.91355, 30.30548 59...       0.0
4021  6309  MULTIPOLYGON (((30.31711 60.01711, 30.31678 60...       7.2
4022  6310  MULTIPOLYGON (((30.30157 59.96321, 30.30233 59...       7.2

[4023 rows x 3 columns]

In [34]:
conditions = [
    (living_blocks['time_min'] < 4),
    (living_blocks['time_min'] >= 4) & (living_blocks['time_min'] < 7),
    (living_blocks['time_min'] >= 7) & (living_blocks['time_min'] < 10),
    (living_blocks['time_min'] >= 10) & (living_blocks['time_min'] < 14),
    (living_blocks['time_min'] >= 14)
    ]

values = [5,4,3,2,1]


living_blocks['mark'] = np.select(conditions, values)
living_blocks

id                                           geometry  time_min  mark
0        2  MULTIPOLYGON (((30.27569 60.01187, 30.27273 60...       0.0     5
1        3  MULTIPOLYGON (((30.37142 59.92849, 30.37013 59...      12.5     2
2        4  MULTIPOLYGON (((30.33351 59.91790, 30.33186 59...       8.4     3
3        5  MULTIPOLYGON (((30.30415 59.96934, 30.30406 59...       5.5     4
4        6  MULTIPOLYGON (((30.36352 59.94154, 30.36056 59...       4.1     4
...    ...                                                ...       ...   ...
4018  6306  MULTIPOLYGON (((30.29618 59.93163, 30.30080 59...       0.0     5
4019  6307  MULTIPOLYGON (((30.36050 59.94085, 30.36048 59...       0.0     5
4020  6308  MULTIPOLYGON (((30.29744 59.91355, 30.30548 59...       0.0     5
4021  6309  MULTIPOLYGON (((30.31711 60.01711, 30.31678 60...       7.2     3
4022  6310  MULTIPOLYGON (((30.30157 59.96321, 30.30233 59...       7.2     3

[4023 rows x 4 columns]

In [35]:
living_blocks.sort_values(by='mark')

id                                           geometry  time_min  mark
2011  2583  MULTIPOLYGON (((30.37331 59.67182, 30.37323 59...      53.5     1
1527  1798  MULTIPOLYGON (((30.26816 59.70416, 30.27009 59...      48.9     1
1526  1797  MULTIPOLYGON (((30.23534 59.67262, 30.23693 59...      25.6     1
2747  4169  MULTIPOLYGON (((30.01495 60.00302, 30.01577 60...      21.9     1
1522  1788  MULTIPOLYGON (((30.22818 59.67055, 30.22812 59...      51.0     1
...    ...                                                ...       ...   ...
1038  1202  MULTIPOLYGON (((30.47352 59.92042, 30.47333 59...       0.0     5
1035  1199  MULTIPOLYGON (((30.39186 60.04114, 30.39886 60...       0.0     5
1032  1196  MULTIPOLYGON (((30.39454 60.00989, 30.40231 60...       0.0     5
1058  1222  MULTIPOLYGON (((30.39271 59.94282, 30.39407 59...       0.0     5
0        2  MULTIPOLYGON (((30.27569 60.01187, 30.27273 60...       0.0     5

[4023 rows x 4 columns]

In [36]:
living_blocks.sort_values(by='mark').to_file(f'sasha_morozov_g1_all_blocks.geojson')

In [2]:
import geopandas as gpd
import numpy as np

/home/gk/.local/lib/python3.8/site-packages/geopandas/_compat.py:112: UserWarning: The Shapely GEOS version (3.10.3-CAPI-1.16.1) is incompatible with the GEOS version PyGEOS was compiled with (3.10.1-CAPI-1.16.0). Conversions between both will be slow.
  warnings.warn(


In [14]:
gdf = gpd.read_file('median_accs_krd.geojson')

In [4]:
gdf

id  median_time   hours  \
0     1913        115.0  2 часа   
1     1914        147.0  3 часа   
2     1915        138.0  3 часа   
3     1916        125.0  3 часа   
4     1917        112.0  2 часа   
...    ...          ...     ...   
5572  4085        127.0  3 часа   
5573  4086        124.0  3 часа   
5574  4094        127.0  3 часа   
5575  4215        126.0  3 часа   
5576  6281        128.0  3 часа   

                                               geometry  
0     MULTIPOLYGON (((30.34279 59.94489, 30.34322 59...  
1     MULTIPOLYGON (((30.37190 60.05315, 30.36964 60...  
2     MULTIPOLYGON (((30.13301 59.99449, 30.13268 59...  
3     MULTIPOLYGON (((30.38280 59.94858, 30.37827 59...  
4     MULTIPOLYGON (((30.27884 59.92001, 30.27740 59...  
...                                                 ...  
5572  MULTIPOLYGON (((30.34138 59.89481, 30.34149 59...  
5573  MULTIPOLYGON (((30.34711 59.88000, 30.34651 59...  
5574  MULTIPOLYGON (((30.38049 59.81848, 30.38040 59...  
5575  MULTIPOLYGON (((30.34195 59.88754, 30.34407 59...  
5576  MULTIPOLYGON (((30.35505 59.89521, 30.35499 59...  

[5577 rows x 4 columns]

In [15]:
conditions = [
    (gdf['median_time'] < 30),
    (gdf['median_time'] >= 30) & (gdf['median_time'] < 45),
    (gdf['median_time'] >= 45) & (gdf['median_time'] < 60),
    (gdf['median_time'] >= 60) & (gdf['median_time'] < 120),
    (gdf['median_time'] >= 120) & (gdf['median_time'] < 180),
    (gdf['median_time'] >= 180) & (gdf['median_time'] < 240),
    (gdf['median_time'] >= 240) & (gdf['median_time'] < 300),
    (gdf['median_time'] >= 300)
    ]

values = [0.5, 0.75, 1, 2, 3, 4, 5, 5.5]


gdf['hours'] = np.select(conditions, values)
gdf

id  median_time  hours  \
0      6577         81.0    2.0   
1      6578         82.0    2.0   
2      6579         82.0    2.0   
3      6580         83.0    2.0   
4      6581         83.0    2.0   
...     ...          ...    ...   
5832  12410         99.0    2.0   
5833  12411         99.0    2.0   
5834  12412        101.0    2.0   
5835  12413        103.0    2.0   
5836  12414        103.0    2.0   

                                               geometry  
0     POLYGON ((38.98198 45.06881, 38.98373 45.06879...  
1     POLYGON ((38.98368 45.05857, 38.98345 45.05803...  
2     POLYGON ((38.98098 45.06629, 38.98098 45.06629...  
3     POLYGON ((38.98106 45.06748, 38.98145 45.06748...  
4     POLYGON ((38.97673 45.06196, 38.97673 45.06196...  
...                                                 ...  
5832  POLYGON ((39.02128 45.02946, 39.02134 45.02938...  
5833  POLYGON ((39.02033 45.03065, 39.02056 45.03034...  
5834  POLYGON ((39.01905 45.03015, 39.01929 45.02948...  
5835  POLYGON ((39.01720 45.02945, 39.01736 45.02920...  
5836  POLYGON ((39.01156 45.02196, 39.01156 45.02196...  

[5837 rows x 4 columns]

In [18]:
# gdf = gdf[~gdf['id'].isin([14794, 14788])]

In [22]:
gdf.explore()

In [13]:
# gdf.rename(columns={'uno': 'median_time'}, inplace=True)

In [16]:
gdf.to_file('median_accs_krd.geojson')